# Автоматическое извлечение коллокаций
## С помощью nltk
Итак, на лекции мы узнали, что такое коллокации.
Теперь мы попытаемся научиться со всем этим работать при помощи nltk, а точнее его подмодуля nltk.collocations.

In [13]:
import nltk # импортируем сам модуль
from nltk.collocations import * # импортируем из модуля все функции для работы с коллокациями
bigram_measures = nltk.collocations.BigramAssocMeasures() # bigram_measures -- набор способов оценки коллокационной связи для биграмм
trigram_measures = nltk.collocations.TrigramAssocMeasures() # то же самое, только для триграмм

_nltk_ &ndash; довольно высокоуровневый модуль, поэтому мы можем дать ему на вход просто текст, поделенный на слова, не выделяя биграммы самим, и он за нас сам разделит наш массив слов на биграммы.

Мы возьмем небольшой корпус, составленный из текстов интернет-новостей. В нем 171 тыс. слов - не очень много, но для экспериментов хватит. Для начала поделим текст на слова просто по пробелам.

In [14]:
words = open('news.txt').read().split()
print(words)

['Губернаторы', 'отвыкли', 'от', 'публичной', 'политики,', 'и', 'их', 'придется', 'учить', 'общаться', 'с', 'избирателями', '—', 'об', 'этом', 'говорили', 'на', 'встрече', 'в', 'Кремле', 'с', 'политологами', 'Вячеслав', 'Володин', 'и', 'другие', 'кураторы', 'внутренней', 'политики.', 'Но', 'недовольство', 'руководства', 'страны', 'вызывают', 'только', 'главы', 'тех', 'регионов,', 'где', 'нет', 'реальной', 'угрозы', 'власти,', 'объясняет', 'участник', 'встречи.', 'С', 'реальными', 'оппонентами', 'местных', 'властей', 'Кремль', 'сам', 'помогает', 'бороться.', 'На', 'встречу', 'с', 'первым', 'замглавы', 'администрации', 'президента', 'Вячеславом', 'Володиным', 'пригласили', 'около', '30', 'политологов,', 'в', 'первую', 'очередь', 'тех,', 'кто', 'назначен', 'Кремлем', 'наблюдать', 'за', 'ходом', 'избирательных', 'кампаний', 'на', 'местах,', 'рассказали', 'РБК', 'несколько', 'участников', 'встречи.', 'По', 'словам', 'собеседников,', 'от', 'администрации', 'президента', 'помимо', 'Володина',

Можно однако вспомнить, что мы тут компьютерные лингвисты, и осуществить простейшую предобработку текста &ndash; очистку от знаков препинания и лемматизацию.

In [15]:
import pymorphy2
morph = pymorphy2.MorphAnalyzer()
punct = '.,!?():;'
words = [word.strip(punct) for word in open('news.txt').read().split()]
words_tagged = [morph.parse(word)[0].normal_form for word in words]
print(words_tagged)

['губернатор', 'отвыкнуть', 'от', 'публичный', 'политика', 'и', 'они', 'прийтись', 'учить', 'общаться', 'с', 'избиратель', '—', 'о', 'это', 'говорить', 'на', 'встреча', 'в', 'кремль', 'с', 'политолог', 'вячеслав', 'володин', 'и', 'другой', 'куратор', 'внутренний', 'политика', 'но', 'недовольство', 'руководство', 'страна', 'вызывать', 'только', 'глава', 'тот', 'регион', 'где', 'нет', 'реальный', 'угроза', 'власть', 'объяснять', 'участник', 'встреча', 'с', 'реальный', 'оппонент', 'местный', 'власть', 'кремль', 'сам', 'помогать', 'бороться', 'на', 'встреча', 'с', 'один', 'замглавы', 'администрация', 'президент', 'вячеслав', 'володин', 'пригласить', 'около', '30', 'политолог', 'в', 'один', 'очередь', 'тот', 'кто', 'назначить', 'кремль', 'наблюдать', 'за', 'ход', 'избирательный', 'кампания', 'на', 'место', 'рассказать', 'рбк', 'несколько', 'участник', 'встреча', 'по', 'слово', 'собеседник', 'от', 'администрация', 'президент', 'помимо', 'володин', 'быть', 'ещё', 'руководитель', 'внутренний',

Так-то лучше. Теперь инициализируем объект класса BigramCollocationFinder, который за нас выделяет в массиве слов биграммы и считает для них всякие характеристики.

In [16]:
finder = BigramCollocationFinder.from_words(words_tagged)

Распечатаем, например, 10 самых сильных коллокаций по версии метрики Pointwise Mutual Information.

Полный набор доступных мер оценки коллокационной связи см. [здесь](http://www.nltk.org/_modules/nltk/metrics/association.html)

In [17]:
finder.nbest(bigram_measures.pmi, 10) # первый аргумент -- метрика, второй аргумент -- количество нужных коллокаций

[('"закручивание', 'гаек"'),
 ('+', '4,65%»'),
 ('0,58', 'евро»'),
 ('12–15', 'контрольно-надзорный'),
 ('1400', 'полувагон'),
 ('1577', 'lada'),
 ('17,2%', 'заболевание'),
 ('18,49%', 'ppf'),
 ('2,68%', '«сделка'),
 ('2010–2020', 'годы)»')]

Видим, что среди мнимых коллокаций попадается много мусора. Попробуем от него избавиться, установив для finder'а фильтр по частотности. Таким образом мы отсеем биграммы, которые встретились в корпусе 1 или 2 раза.

In [6]:
finder.apply_freq_filter(3) # смотрим только на биграммы, которые встретились 3+ раз
finder.nbest(bigram_measures.pmi, 10)

[('kyodo', 'news'),
 ('ponars', 'eurasia'),
 ('small', 'letters'),
 ('synovate', 'comcon'),
 ('«наблюдатель', 'петербурга»'),
 ('«негативный', 'консенсус»'),
 ('«утрата', 'доверия»'),
 ('андерс', 'фог'),
 ('гаснуть', '«выборы»'),
 ('goltsblat', 'blp')]

Так-то лучше, но ещё есть, что улучшать. Например, можем удалить из коллокаций стоп-слова (предлоги, союзы, местоимения) и просто слова короче 3 символов.

Заодно помимо pmi попробуем ещё другую метрику &ndash; Log-Likelihood.

Для начала скачаем стоп-слова:

In [8]:
nltk.download()

NLTK Downloader
---------------------------------------------------------------------------
    d) Download   l) List    u) Update   c) Config   h) Help   q) Quit
---------------------------------------------------------------------------
Downloader> d

Download which package (l=list; x=cancel)?
  Identifier> stopwords
      Unzipping corpora/stopwords.zip.

---------------------------------------------------------------------------
    d) Download   l) List    u) Update   c) Config   h) Help   q) Quit
---------------------------------------------------------------------------
Downloader> q


True

In [9]:
stopwords = nltk.corpus.stopwords.words('russian') # в нлтк есть готовые списки стоп-слов, в том числе для русского языка
finder.apply_word_filter(lambda w: len(w) < 3 or w.lower() in stopwords) # отсеиваем биграммы, которые встретились меньше трёх раз или которые содержат стоп-слова
finder.nbest(bigram_measures.likelihood_ratio, 10) # ищем 10 лучших согласно метрике log-likelihood

[('миллиард', 'рубль'),
 ('2014', 'год'),
 ('2013', 'год'),
 ('2015', 'год'),
 ('точка', 'зрение'),
 ('сказать', 'рбк'),
 ('миллион', 'рубль'),
 ('владимир', 'путин'),
 ('«единый', 'россии»'),
 ('афк', '«система»')]

До сих пор мы распечатывали N биграмм, имеющих наибольшую меру коллокационной связи. Но можно распечатать и все биграммы и их оценки.

Допустим, мы хотим распечатать просто частоту биграммы в корпусе.

*raw_freq &ndash; метод, который ранжирует биграммы по количеству вхождений в тексте*

In [10]:
scored_bigrams = finder.score_ngrams(bigram_measures.raw_freq) # score_ngrams возвращает нам N-граммы с оценками
sorted(scored_bigrams, key = lambda x: x[1]) # сортируем список по оценке

[(('$1,5', 'миллиард'), 1.6956624953369282e-05),
 (('$10', 'миллиард'), 1.6956624953369282e-05),
 (('$25', 'миллион'), 1.6956624953369282e-05),
 (('$30', 'миллион'), 1.6956624953369282e-05),
 (('$50', 'миллиард'), 1.6956624953369282e-05),
 (('0,5', 'п.п'), 1.6956624953369282e-05),
 (('1,5', 'миллиард'), 1.6956624953369282e-05),
 (('1,5', 'триллион'), 1.6956624953369282e-05),
 (('1,6', 'миллиард'), 1.6956624953369282e-05),
 (('1,8', 'миллиард'), 1.6956624953369282e-05),
 (('120', 'тысяча'), 1.6956624953369282e-05),
 (('19.00', 'мск'), 1.6956624953369282e-05),
 (('1992', 'год'), 1.6956624953369282e-05),
 (('1998', 'год'), 1.6956624953369282e-05),
 (('2,3', 'миллиард'), 1.6956624953369282e-05),
 (('2,99', 'миллиард'), 1.6956624953369282e-05),
 (('200', 'километр'), 1.6956624953369282e-05),
 (('2012–2013', 'год'), 1.6956624953369282e-05),
 (('2017', 'годов»'), 1.6956624953369282e-05),
 (('2030', 'год'), 1.6956624953369282e-05),
 (('3,8', 'миллиард'), 1.6956624953369282e-05),
 (('300', 'мил

Допустим, нас интересуют биграммы, частотность которых больше, чем какой-то порог.

In [11]:
frequent_bigrams = finder.above_score(bigram_measures.raw_freq, 0.0005) # найди биграммы с оценкой больше, чем 0.0005
for b in frequent_bigrams:
    print(b)

('миллиард', 'рубль')
('2014', 'год')
('2013', 'год')
('2015', 'год')
('миллион', 'рубль')
('сказать', 'рбк')
('это', 'год')


Все, что мы до настоящего момента делали на материале биграмм, можно сделать и с триграммами. В nltk для них доступны аналогичные функции.

For your interest: в nltk есть ещё и функции для 4-грамм, которые там называются Quadgram.

In [12]:
tr_finder = TrigramCollocationFinder.from_words(words_tagged)
tr_finder.apply_word_filter(lambda w: len(w) < 3 or w.lower() in stopwords)
tr_finder.apply_freq_filter(10)
tr_finder.nbest(trigram_measures.likelihood_ratio, 10)

[('квартал', '2014', 'год'),
 ('полугодие', '2014', 'год'),
 ('конец', '2014', 'год'),
 ('апрель', '2014', 'год'),
 ('начало', '2014', 'год'),
 ('сентябрь', '2014', 'год'),
 ('точка', 'зрение', 'автор'),
 ('сказать', 'рбк', 'представитель'),
 ('президент', 'владимир', 'путин'),
 ('сказать', 'рбк', 'источник')]

Ну ок. Научились мы извлекать коллокации, но бездумно это делать не хочется. Как же это работает?

На самом деле, когда мы создаем объект класса CollocationFinder, он берет все биграммы/триграммы/whatever в наших данных и считает для них для всех несколько характеристик.

Затем, когда мы запрашиваем какую-то меру коллокационной связи, nltk берет эти характеристики и считает нужную нам меру.

Что это за характеристики?

На самом деле nltk считает для каждой пары слов в массиве такую матрицу: частота слова1 в корпусе, частота слова2 в корпусе, частота совместной встречаемости слова1 и слова2 в корпусе, общее количество биграмм в корпусе.
Затем, когда мы запрашиваем коллокации с какими-то характеристиками, nltk быстренько их подсчитывает, поскольку готовые данные у него уже есть, и отдает нам результат.

In [ ]:
import time